# Real Time Tweet Analysis & Dashboarding Tool (2/2)
## How to Use the Tool
Running all cells in this notebook, 'DATS 6103 - Project 3 Analysis.ipynb' reads the .csv file into a dataframe and performs the analysis.  The end of this file gives a dashboard showing real time information about Tweets containing the tracked word.  One can keep running all cells in this notebook to update the dashboard as new Tweets are constantly being streamed from 'DATS 6103 - Project 3 Streaming' notebook.

## Importing Libraries

In [113]:
import pandas as pd
import numpy as np

import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

import itertools

import nltk
from nltk.probability import FreqDist
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
nltk.download('punkt')

[nltk_data] Downloading package punkt to
[nltk_data]     /Users/jonathangiguere/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

## Create DataFrame from  OutputStreaming.csv
OutputStreaming.csv should be constantly growing as new tweets get added from the 'DATS 6103 - Project 3 Streaming' notebook.  Each time this cell runs, the length of the dataframe is returned to show how the file is growing.  

In [114]:
#Read csv file made by StreamListener object into pandas dataframe
tweet_df = pd.read_csv('OutputStreaming.csv', index_col=False)
len(tweet_df)

19658

## Visualizing the Data
### 1) Tweets per Minute
In order to get tweets per minute, I grouped the dataframe by 60 second intervals and got the count of tweets for each interval.  I used Plotly Express and Plotly graph_objects to create all visualizations in this report.

In [115]:
#Convert date to pandas date type
tweet_df['Date'] = pd.to_datetime(tweet_df['Date'])

#Gives dataframe of rows as minute intervals and counts tweets in each interval
tweets_per_min = tweet_df.groupby([pd.Grouper(key = 'Date', freq='60s', base=0)]).count().drop(['Text',
                                        'Retweet?', 'Polarity_SW', 'Polarity_NSW',
                                        'User Location', 'User_Follower_Count', 'Longitude',
                                        'Latitude'], axis=1).reset_index()

#Rename columns so you can see the minutes and tweets
tweets_per_min = tweets_per_min.rename(columns = {'Date':'Minute', 'Author':'Tweets'})

In [116]:
#Make line chart showing tweets per minute
fig = px.line(tweets_per_min, x='Minute', y="Tweets")
fig.show()

### 2) Average Polarity Score per Minute
To visualize this, I first split the dataframe into positive, negative, and neutral tweets.  I grouped the data by 60 second intervals, added the positive, neutral, and negative scores up,  and then divided by the number of tweets in that minute to get the average minutely polarity score for tweets containing the tracked word. 

In [117]:
#Gets list of boolean values for filtering
neg_filter = tweet_df['Polarity_SW'] < 0
neutral_filter = tweet_df['Polarity_SW'] == 0
pos_filter = tweet_df['Polarity_SW'] > 0

#Use filters to get lists of polarity scores
neg_tweet_scores = tweet_df[neg_filter].iloc[:,4] 
neutral_tweet_scores = tweet_df[neutral_filter].iloc[:,4] 
pos_tweet_scores = tweet_df[pos_filter].iloc[:,4] 

dict_ = {'Negative':neg_tweet_scores, 'Neutral':neutral_tweet_scores, 'Positive':pos_tweet_scores, 
         'Time':tweet_df['Date']}

#Create scores dataframe
polarity_df = pd.DataFrame(data=dict_)

#Change all NAs to 0's so we can add them up for different time intervals
polarity_df = polarity_df.fillna(0)

#Groups dataframe into 60 second intervals and sums all the scores for each interval
polarity_df = polarity_df.groupby([pd.Grouper(key = 'Time', freq='60s', base=0)]).sum()

#Create new column that adds up scores from all sentiment categories
polarity_df['scores'] = polarity_df['Negative'] + polarity_df['Neutral'] + polarity_df['Positive']

#Append tweets per minute to dataframe from above
polarity_df['tweets_per_min'] = tweets_per_min['Tweets'].values

#Using the combined score per minute, and the tweets per minute, get avg sentiment per minute
polarity_df['avg_score'] = (polarity_df['scores'] / polarity_df['tweets_per_min'])

#Reset index so Time is its own column
polarity_df = polarity_df.reset_index()

In [118]:
#Make line chart showing average sentiment per minute for the keyword
fig = px.line(polarity_df, x='Time', y="avg_score")
fig.update_xaxes(zeroline=True, zerolinewidth=2)
fig.show()

### 3) Number of Positive, Negative, and Neutral Tweets Per 20 Seconds
To visualize this, I grouped the original dataframe 'tweet_df' by 20 second intervals.  Next, I performed similar steps from visual 1 where I got the number of tweets for each time interval, but this time I got the number of tweets for each given polarity category: neutral (polarity=0), positive (polarity>0), and negative (polarity<0).  The resulting chart shows lines for the number of each type of tweet posted in 20 second time intervals.

In [119]:
#Start over with original df
tweet_df

#Group by the minute, get rid of all columns other than Date and Polarity_SW and Author
#Unstack and replace NA's with 0's...this makes each minute a row and the number of tweets for each 
#          sentiment score the entries in the rows
sep_scores_df = tweet_df.groupby([pd.Grouper(key = 'Date', freq='20s'), 'Polarity_SW']).count().drop(
['Text', 'Retweet?', 'Polarity_NSW', 'User Location', 'User_Follower_Count', 'Longitude',
'Latitude'], axis=1).unstack(fill_value=0)

#Restack data and reset index to get Date as its own column
sep_scores_df = sep_scores_df.stack().reset_index()

#Rename Author column to reflect that it is the number of tweets with the corresponding score
sep_scores_df = sep_scores_df.rename(columns = {"Author":"Tweets"})

#Create new column for classifying negative, pos, and neutral score categories
conditions = [
    (sep_scores_df['Polarity_SW'] == 0),
    (sep_scores_df['Polarity_SW'] > 0),
    (sep_scores_df['Polarity_SW'] < 0)]
choices = ['Neutral', 'Positive', 'Negative']
sep_scores_df['Pol_Category'] = np.select(conditions, choices)

In [120]:
fig = px.line(sep_scores_df, x='Date', y="Tweets",            
    color='Pol_Category')
fig.show()

### 4) Number of Positive and Negative Tweets Per 20 Seconds
I noticed that when visualizing all three categories of tweets at the same time, there were always a significant amount of neutral tweets.  Because I am trying to analyze how Twitter users feel about the tracked word, I figured it would be better to only compare the amounts of negative and positive tweets.

In [121]:
#Plot only Negative and Positive Tweets

#Remove neutral rows
neg_pos_df = sep_scores_df[sep_scores_df['Pol_Category'] != 'Neutral']

#Plot the neg and pos tweets
fig = px.line(neg_pos_df, x='Date', y="Tweets",            
    color='Pol_Category')
fig.show()

### 5) US States Tweeting about the Keyword
To visualize the tweets per state, I read in a file 'us_states.csv' and ultimately convert it to a dictionary.  I also specify that we do not want retweets to be in this visual.  I think that including retweets would artificially inflate the amount of tweets coming from a state.  It is important to note that the rest of the visuals include retweets but they can be easily excluded right after reading in the 'OutputStreaming.csv' file if you would like.    

In [122]:
#Read in data from states csv file
state_df = pd.read_csv('us_states.csv')

#Convert states to list
state_list = list(state_df['State'])

#Create dictionary from list of states and abreviations
state_dict = dict(itertools.zip_longest(*[iter(state_list)] * 2, fillvalue=""))

#Get a df with no retweets.  Heavily retweeted tweets might inflate numbers.
no_retweet_df = tweet_df[tweet_df['Retweet?'] == False]

Here, I loop through the 'User Location' column in the dataframe and the list of state names and abbreviations to compare.  If the state name or abbreviation is in the particular tweet's 'User Location' field, the state's abbreviation is appended to the list from the state dicitonary created above.  If there is no match, nothing is appended to the list.  I convert the new list to a dataframe, drop all NA values, and group by the count of each state.  

In [123]:
#Initialize list to keep track of users with locations in the US
is_in_US=[]

#Fill all na values with an empty string in the main df
no_retweet_df = no_retweet_df.fillna(" ")

#Loop through each user location for each tweet
for x in no_retweet_df['User Location']:
    check = False
    #Loop through list of states and abbreviations
    for s in state_list:
        #If the state name or abbreviation appears in the tweet location append state abr to list
        if s in x:
            is_in_US.append(state_dict[s] if s in state_dict else s)
            check = True
            break
    #If check is False, meaning the state or abr is not in the tweet user location, append None
    if not check:
        is_in_US.append(None)

#Create dataframe from the list created in the for loop
#Remove all NA values and reset index to prepare for grouping
loc_in_US_df = pd.DataFrame(is_in_US, columns = ['State']).dropna().reset_index()

#Group dataframe by state and get the counts of each state
loc_in_US_df = loc_in_US_df.groupby('State').count().rename(columns={'index':'Num_Tweets'})

#Sort values in descending order and reset index
loc_in_US_df = loc_in_US_df.sort_values(by=['Num_Tweets'], ascending=False).reset_index()

The cell below demonstrates the use of Plotly to create the map of the US.  It is important to note that many Twitter users either do not have a location on their profile or do not have a meaningful location.  This means that when streaming tweets, the map will display fewer tweets than the number of tweets streamed.    

In [124]:
#Plot heatmap of states with most tweets about the tracked word
fig = go.Figure(data=go.Choropleth(
    locations = loc_in_US_df['State'], 
    #Data to be colored on map
    z = loc_in_US_df['Num_Tweets'].astype(float),

    locationmode = 'USA-states', 
    colorscale = "Greens",
    marker_line_color='white', # line markers between states
    colorbar_title = "Number of Tweets"
))

fig.update_layout(
    geo_scope='usa', 
)

fig.show()

### 6) 10 Most Frequently Occuring Words
In order to get the most frequently occuring words, I combined all the text from the tweets into one corpus, did some additional cleaning that was not handled when the tweets were streamed, made all words lowercase, tokenized the lowercase words, and then used the FreqDist() function from nltk to see which words were the top ten.  I assigned the top ten words to a dataframe and plotted it as a barchart.

In [125]:
#Initialize list to hold all words
all_words = []

#Only append to list if the tweet text is of string type
for i in tweet_df['Text'].values:
    if isinstance(i, str):
        all_words.append(i)

#Join all elements of the list to make one one corpus
all_words = ' '.join(all_words)

#Replace ampersands with and
all_words = all_words.replace('&amp;', 'and')

#Clean up some additional things that were not cleaned up when the tweets were streamed
all_words = all_words.replace('.', '')
all_words = all_words.replace("'s", '')
all_words = all_words.replace(',', '')
all_words = all_words.replace('?', '')
all_words = all_words.replace('+', '')

#Convert all words to lowercase
all_words = all_words.lower()

#Tokenize all the individual words in the corpus of all the tweets
token_words = word_tokenize(all_words)

#Gets frequency distribution using nltk
word_freq_dist = FreqDist(token_words)

#Reurns the ten most occuring words from the frequence distribution
word_freq_df = pd.DataFrame(word_freq_dist.most_common(10), columns = ["Word","Frequency"]).drop([0]).reindex()

In [126]:
fig = px.bar(word_freq_df, x="Word", y="Frequency")
fig.update_traces(marker_color='rgb(240,128,128)', marker_line_color='rgb(8,48,107)',
    marker_line_width=1.5, opacity=0.8)
fig.show()

## The Dashboard
Here is the code that creates subplots for the dashboard, and adds the visuals to each subplot.  Above, I used Plotly Express for a few visuals but here I have to use Plotly GO.  Because of this, I made a few quick dataframes to plot the negative and positive tweets in the dashboard with Plotly Go.

All of the different pieces of the dashboard are commented below.  

In [127]:
#Get df of just positive tweets
pos_df = neg_pos_df[neg_pos_df['Pol_Category'] != 'Negative']

#Get df of just negative tweets
neg_df = neg_pos_df[neg_pos_df['Pol_Category'] != 'Positive']

In [128]:
#Create subplots
fig = make_subplots(
        rows=2, cols=2,
        column_widths=[1, 0.4],
        row_heights=[0.6, 1],
        specs=[[{"type": "scatter", "rowspan": 1}, 
                {"type": "choropleth"}],
               [{"type": "scatter", "rowspan": 1}, {"type": "bar"}]]
        )

#Add positive tweet tracking to top left of dash
fig.add_trace(go.Scatter(
    x = pos_df['Date'],
    y = pos_df['Tweets'],
    name = "Positive Tweets",
    opacity = 0.8, marker_color='rgb(152,251,152)'), row = 1, col = 1)

#Add negative tweet tracking to top left of dash
fig.add_trace(go.Scatter(
    x = neg_df['Date'],
    y = neg_df['Tweets'],
    name = "Negative Tweets",
    opacity=0.8, marker_color='rgb(255,0,0)'), row=1, col=1)

#Add bar chart to top right of dash
fig.add_trace(go.Bar(x=word_freq_df["Word"], y = word_freq_df["Frequency"],
    name = "Words Occuring the Most"), row = 2, col = 2)

#Update formatting of bar chart
fig.update_traces(marker_color = 'rgb(152,251,152)',
    marker_line_color = 'rgb(8,48,107)',  
    marker_line_width = 0.5, opacity=0.7, row=2, col=2)

#Add Map to top right of dash
fig.add_trace(go.Choropleth(
    locations= loc_in_US_df['State'], # Spatial coordinates
    z = loc_in_US_df['Num_Tweets'].astype(float), # Data to be color-coded
    locationmode = 'USA-states', 
    colorscale = "Greens",
    showscale = False,
    geo = 'geo'
    ), row=1, col=2)

#Add total number of tweets per min to bottom left of dash
fig.add_trace(go.Scatter(
    x = tweets_per_min['Minute'],
    y = tweets_per_min['Tweets'],
    name = "Tweets per Minute",
    opacity = 0.8, marker_color='rgb(152,251,152)'), row = 2, col = 1)

#Change scope of map so that is only shows US
fig.update_layout(
    title_text = 'Keyword Twitter Mention Dashboard',
    geo_scope = 'usa',
    template = 'plotly_dark',
    margin=dict(r=20, t=50, b=50, l=20),
    showlegend = False
    )

fig.show()

### Dashboard Interpretation and Use
Hover over any part of the dashboard to get tooltips showing important information at each point.  One can drag a box over the line and bar charts to get a zoomed in view of a subset of data points (double click to zoom out).

I recommend streaming tweets for 10-15 minutes before looking at this dashboard.  Time needs to pass to allow the time series graphs to gain some aesthetic improvement.

The Twitter API gives timestamps in GMT.  Greenwich Mean Time is five hours ahead of Eastern Standard Time (I am located on the East Coast).

Quadrant Descriptions:
- Top-Left: The number of positive and negative tweets occuring every 20 seconds.
- Bottom-Left: The number of tweets containing the keyword occuring every minute.
- Top-Right: The number of tweets containing the tracked word from each state.
- Bottom-Right: The ten most frequently occuring words in the tweets containing the tracked word.
